In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, ExtraTreesClassifier
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix, f1_score, precision_score, recall_score, roc_auc_score
import numpy as np

In [2]:
# Read the CSV file into a dataframe
data = pd.read_csv('credit_card_transactions.csv')

# Display the first few records
data.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ...      long city_pop  \
0    Banks      F                561 Perry Cove  ...  -81.1781     3495   
1     Gill      F  43039 Riley Greens Suite 393  ... -118.2105      149   
2  Sanchez      M      594 White Dale Suite 530  ... -112.2620     4154   
3    White      M   9443 Cynthia Court Apt. 038  ... -112.1138     1939   
4   Garcia      M              408 Bradley Rest  ...  -79.4629       99   

                                 job         dob  \
0          Psychologist, counselling  1988-03-09   
1  Special educational needs teacher  1978-06-21   
2        Nature conservation officer  1962-01-19   
3                    Patent attorney  1967-01-12   
4     Dance movement psychotherapist  1986-03-28   

                          trans_num   unix_time  merch_lat  merch_long  \
0  0b242abb623afc578575680df30655b9  1325376018  36.011293  -82.048315   
1  1f76529f8574734946361c461b024d99  1325376044  49.159047 -118.186462   
2  a1a22d70485983eac12b5b88dad1cf95  1325376051  43.150704 -112.154481   
3  6b849c168bdad6f867558c3793159a81  1325376076  47.034331 -112.561071   
4  a41d7549acf90789359a9aa5346dcb46  1325376186  38.674999  -78.632459   

  is_fraud  merch_zipcode  
0        0        28705.0  
1        0            NaN  
2        0        83236.0  
3        0            NaN  
4        0        22844.0  

[5 rows x 24 columns]

In [3]:
# Explore data columns
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1296675 entries, 0 to 1296674
Data columns (total 24 columns):
 #   Column                 Non-Null Count    Dtype  
---  ------                 --------------    -----  
 0   Unnamed: 0             1296675 non-null  int64  
 1   trans_date_trans_time  1296675 non-null  object 
 2   cc_num                 1296675 non-null  int64  
 3   merchant               1296675 non-null  object 
 4   category               1296675 non-null  object 
 5   amt                    1296675 non-null  float64
 6   first                  1296675 non-null  object 
 7   last                   1296675 non-null  object 
 8   gender                 1296675 non-null  object 
 9   street                 1296675 non-null  object 
 10  city                   1296675 non-null  object 
 11  state                  1296675 non-null  object 
 12  zip                    1296675 non-null  int64  
 13  lat                    1296675 non-null  float64
 14  long              

In [4]:
# function to get number of unique values for each column ..
# to determine what kind of encoding and imputation needs to be done!

def display_unique_values(data):
    """
    Display unique values and the number of unique values for each column in the dataframe.

    Parameters:
    data (pd.DataFrame): The dataframe to analyze.

    Returns:
    None
    """
    for column in data.columns:
        unique_values = data[column].unique()
        print(f"Column: {column}")
        print(f"Data Type: {data[column].dtype}")
        print(f"Number of Unique Values: {len(unique_values)}")
        print(f"Unique Values: {unique_values[:10]}...")  # Show the first 10 unique values for brevity
        print("-" * 50)

# Display details of each column:
display_unique_values(data)

Column: Unnamed: 0
Data Type: int64
Number of Unique Values: 1296675
Unique Values: [0 1 2 3 4 5 6 7 8 9]...
--------------------------------------------------
Column: trans_date_trans_time
Data Type: object
Number of Unique Values: 1274791
Unique Values: ['2019-01-01 00:00:18' '2019-01-01 00:00:44' '2019-01-01 00:00:51'
 '2019-01-01 00:01:16' '2019-01-01 00:03:06' '2019-01-01 00:04:08'
 '2019-01-01 00:04:42' '2019-01-01 00:05:08' '2019-01-01 00:05:18'
 '2019-01-01 00:06:01']...
--------------------------------------------------
Column: cc_num
Data Type: int64
Number of Unique Values: 983
Unique Values: [2703186189652095     630423337322   38859492057661 3534093764340240
  375534208663984 4767265376804500   30074693890476 6011360759745864
 4922710831011201 2720830304681674]...
--------------------------------------------------
Column: merchant
Data Type: object
Number of Unique Values: 693
Unique Values: ['fraud_Rippin, Kub and Mann' 'fraud_Heller, Gutmann and Zieme'
 'fraud_Lind-Buckr

In [5]:
# Make a copy for transformation
ak_df = data.copy()

# Convert date columns to datetime format
ak_df['trans_date_trans_time'] = pd.to_datetime(ak_df['trans_date_trans_time'])
ak_df['dob'] = pd.to_datetime(ak_df['dob'])

In [6]:
# AGE - Calculate age based on DOB and transaction year
ak_df['ft_age'] = ak_df['trans_date_trans_time'].dt.year - ak_df['dob'].dt.year

# AGE SEGMENT - Define age segments
def age_segment(age):
    if age < 18:
        return 'Under 18'
    elif 19 <= age <= 28:
        return '19-28'
    elif 29 <= age <= 38:
        return '29-38'
    elif 39 <= age <= 48:
        return '39-48'
    elif 49 <= age <= 58:
        return '49-58'
    elif 59 <= age <= 68:
        return '59-68'
    elif 69 <= age <= 78:
        return '69-78'
    else:
        return '79+'

# Apply age segmentation
ak_df['ft_age_group'] = ak_df['ft_age'].apply(age_segment)

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ...  \
0    Banks      F                561 Perry Cove  ...   
1     Gill      F  43039 Riley Greens Suite 393  ...   
2  Sanchez      M      594 White Dale Suite 530  ...   
3    White      M   9443 Cynthia Court Apt. 038  ...   
4   Garcia      M              408 Bradley Rest  ...   

                                 job        dob  \
0          Psychologist, counselling 1988-03-09   
1  Special educational needs teacher 1978-06-21   
2        Nature conservation officer 1962-01-19   
3                    Patent attorney 1967-01-12   
4     Dance movement psychotherapist 1986-03-28   

                          trans_num   unix_time  merch_lat  merch_long  \
0  0b242abb623afc578575680df30655b9  1325376018  36.011293  -82.048315   
1  1f76529f8574734946361c461b024d99  1325376044  49.159047 -118.186462   
2  a1a22d70485983eac12b5b88dad1cf95  1325376051  43.150704 -112.154481   
3  6b849c168bdad6f867558c3793159a81  1325376076  47.034331 -112.561071   
4  a41d7549acf90789359a9aa5346dcb46  1325376186  38.674999  -78.632459   

  is_fraud merch_zipcode ft_age  ft_age_group  
0        0       28705.0     31         29-38  
1        0           NaN     41         39-48  
2        0       83236.0     57         49-58  
3        0           NaN     52         49-58  
4        0       22844.0     33         29-38  

[5 rows x 26 columns]

In [7]:
# TRANSACTION HOUR
ak_df['ft_trans_hour'] = ak_df['trans_date_trans_time'].dt.hour

# TIME OF DAY - Categorize time of day based on transaction hour
ak_df['ft_time_of_day'] = ak_df['trans_date_trans_time'].dt.hour.apply(
    lambda hour: 'Morning' if 6 <= hour < 12 else
    ('Afternoon' if 12 <= hour < 18 else
    ('Evening' if 18 <= hour < 24 else 'Night'))
)

# TRANSACTION DAY
ak_df['ft_trans_day'] = ak_df['trans_date_trans_time'].dt.day

# TRANSACTION DAY OF YEAR
ak_df['ft_trans_day_of_year'] = ak_df['trans_date_trans_time'].dt.dayofyear

# TRANSACTION MONTH
ak_df['ft_trans_month'] = ak_df['trans_date_trans_time'].dt.month

# DAY OF WEEK - Add a new column 'day_of_week' to represent the day of the week (0=Monday, 6=Sunday)
ak_df['ft_day_of_week'] = ak_df['trans_date_trans_time'].dt.day_name()


ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... is_fraud merch_zipcode  \
0    Banks      F                561 Perry Cove  ...        0       28705.0   
1     Gill      F  43039 Riley Greens Suite 393  ...        0           NaN   
2  Sanchez      M      594 White Dale Suite 530  ...        0       83236.0   
3    White      M   9443 Cynthia Court Apt. 038  ...        0           NaN   
4   Garcia      M              408 Bradley Rest  ...        0       22844.0   

   ft_age  ft_age_group  ft_trans_hour  ft_time_of_day ft_trans_day  \
0      31         29-38              0           Night            1   
1      41         39-48              0           Night            1   
2      57         49-58              0           Night            1   
3      52         49-58              0           Night            1   
4      33         29-38              0           Night            1   

  ft_trans_day_of_year ft_trans_month  ft_day_of_week  
0                    1              1         Tuesday  
1                    1              1         Tuesday  
2                    1              1         Tuesday  
3                    1              1         Tuesday  
4                    1              1         Tuesday  

[5 rows x 32 columns]

In [8]:
# DISTANCE BETWEEN USER AND MERCHANT

import numpy as np

# Define the Haversine Formula function that calculates the distance given two latitude/longitude points
def haversine(lat1, lon1, lat2, lon2):
    # Convert latitude and longitude from degrees to radians
    lat1, lon1, lat2, lon2 = map(np.radians, [lat1, lon1, lat2, lon2])

    # Haversine formula
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = np.sin(dlat / 2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    radius = 6371  # Radius of Earth in kilometers
    return radius * c

# Create a new column for distance
ak_df['ft_distance_user_merchant'] = haversine(
    ak_df['lat'], ak_df['long'],
    ak_df['merch_lat'], ak_df['merch_long']
)

# Calculate the average distance of previous transactions for a user and compare the current transaction distance
user_avg_distance = ak_df.groupby('cc_num')['ft_distance_user_merchant'].transform('mean')
ak_df['ft_merchant_distance_from_user_mean'] = ak_df['ft_distance_user_merchant'] - user_avg_distance


ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_age ft_age_group  \
0    Banks      F                561 Perry Cove  ...     31        29-38   
1     Gill      F  43039 Riley Greens Suite 393  ...     41        39-48   
2  Sanchez      M      594 White Dale Suite 530  ...     57        49-58   
3    White      M   9443 Cynthia Court Apt. 038  ...     52        49-58   
4   Garcia      M              408 Bradley Rest  ...     33        29-38   

   ft_trans_hour  ft_time_of_day  ft_trans_day  ft_trans_day_of_year  \
0              0           Night             1                     1   
1              0           Night             1                     1   
2              0           Night             1                     1   
3              0           Night             1                     1   
4              0           Night             1                     1   

  ft_trans_month ft_day_of_week ft_distance_user_merchant  \
0              1        Tuesday                 78.597568   
1              1        Tuesday                 30.212176   
2              1        Tuesday                108.206083   
3              1        Tuesday                 95.673231   
4              1        Tuesday                 77.556744   

   ft_merchant_distance_from_user_mean  
0                             0.637376  
1                           -41.580370  
2                            34.130756  
3                            23.971060  
4                             2.322402  

[5 rows x 34 columns]

In [9]:
# Count the number of transactions for each merchant in the dataset
merchant_transaction_counts = ak_df['merchant'].value_counts()
ak_df['ft_merchant_popularity'] = ak_df['merchant'].map(merchant_transaction_counts)

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_age_group  \
0    Banks      F                561 Perry Cove  ...        29-38   
1     Gill      F  43039 Riley Greens Suite 393  ...        39-48   
2  Sanchez      M      594 White Dale Suite 530  ...        49-58   
3    White      M   9443 Cynthia Court Apt. 038  ...        49-58   
4   Garcia      M              408 Bradley Rest  ...        29-38   

  ft_trans_hour  ft_time_of_day  ft_trans_day  ft_trans_day_of_year  \
0             0           Night             1                     1   
1             0           Night             1                     1   
2             0           Night             1                     1   
3             0           Night             1                     1   
4             0           Night             1                     1   

   ft_trans_month ft_day_of_week ft_distance_user_merchant  \
0               1        Tuesday                 78.597568   
1               1        Tuesday                 30.212176   
2               1        Tuesday                108.206083   
3               1        Tuesday                 95.673231   
4               1        Tuesday                 77.556744   

  ft_merchant_distance_from_user_mean  ft_merchant_popularity  
0                            0.637376                    1267  
1                          -41.580370                    2503  
2                           34.130756                    1895  
3                           23.971060                    2613  
4                            2.322402                    1592  

[5 rows x 35 columns]

In [10]:
# Calculate the mean transaction amount for each user (cc_num)
user_mean_amt = ak_df.groupby('cc_num')['amt'].transform('mean')
ak_df['ft_mean_amt_per_user'] = user_mean_amt

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_trans_hour  \
0    Banks      F                561 Perry Cove  ...             0   
1     Gill      F  43039 Riley Greens Suite 393  ...             0   
2  Sanchez      M      594 White Dale Suite 530  ...             0   
3    White      M   9443 Cynthia Court Apt. 038  ...             0   
4   Garcia      M              408 Bradley Rest  ...             0   

  ft_time_of_day  ft_trans_day  ft_trans_day_of_year  ft_trans_month  \
0          Night             1                     1               1   
1          Night             1                     1               1   
2          Night             1                     1               1   
3          Night             1                     1               1   
4          Night             1                     1               1   

   ft_day_of_week ft_distance_user_merchant  \
0         Tuesday                 78.597568   
1         Tuesday                 30.212176   
2         Tuesday                108.206083   
3         Tuesday                 95.673231   
4         Tuesday                 77.556744   

  ft_merchant_distance_from_user_mean ft_merchant_popularity  \
0                            0.637376                   1267   
1                          -41.580370                   2503   
2                           34.130756                   1895   
3                           23.971060                   2613   
4                            2.322402                   1592   

   ft_mean_amt_per_user  
0             87.393215  
1             53.949320  
2             65.870040  
3             72.776673  
4             95.178091  

[5 rows x 36 columns]

In [11]:
# Calculate the deviation of the transaction amount from the user’s mean transaction amount
ak_df['ft_amt_deviation'] = ak_df['amt'] - ak_df['ft_mean_amt_per_user']

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_time_of_day  \
0    Banks      F                561 Perry Cove  ...          Night   
1     Gill      F  43039 Riley Greens Suite 393  ...          Night   
2  Sanchez      M      594 White Dale Suite 530  ...          Night   
3    White      M   9443 Cynthia Court Apt. 038  ...          Night   
4   Garcia      M              408 Bradley Rest  ...          Night   

  ft_trans_day  ft_trans_day_of_year  ft_trans_month  ft_day_of_week  \
0            1                     1               1         Tuesday   
1            1                     1               1         Tuesday   
2            1                     1               1         Tuesday   
3            1                     1               1         Tuesday   
4            1                     1               1         Tuesday   

   ft_distance_user_merchant ft_merchant_distance_from_user_mean  \
0                  78.597568                            0.637376   
1                  30.212176                          -41.580370   
2                 108.206083                           34.130756   
3                  95.673231                           23.971060   
4                  77.556744                            2.322402   

  ft_merchant_popularity ft_mean_amt_per_user  ft_amt_deviation  
0                   1267            87.393215        -82.423215  
1                   2503            53.949320         53.280680  
2                   1895            65.870040        154.239960  
3                   2613            72.776673        -27.776673  
4                   1592            95.178091        -53.218091  

[5 rows x 37 columns]

In [12]:
# Count the number of transactions for each user (cc_num)
user_transaction_count = ak_df['cc_num'].value_counts()
ak_df['ft_transaction_count_per_user'] = ak_df['cc_num'].map(user_transaction_count)

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_trans_day  \
0    Banks      F                561 Perry Cove  ...            1   
1     Gill      F  43039 Riley Greens Suite 393  ...            1   
2  Sanchez      M      594 White Dale Suite 530  ...            1   
3    White      M   9443 Cynthia Court Apt. 038  ...            1   
4   Garcia      M              408 Bradley Rest  ...            1   

  ft_trans_day_of_year  ft_trans_month  ft_day_of_week  \
0                    1               1         Tuesday   
1                    1               1         Tuesday   
2                    1               1         Tuesday   
3                    1               1         Tuesday   
4                    1               1         Tuesday   

   ft_distance_user_merchant  ft_merchant_distance_from_user_mean  \
0                  78.597568                             0.637376   
1                  30.212176                           -41.580370   
2                 108.206083                            34.130756   
3                  95.673231                            23.971060   
4                  77.556744                             2.322402   

  ft_merchant_popularity ft_mean_amt_per_user ft_amt_deviation  \
0                   1267            87.393215       -82.423215   
1                   2503            53.949320        53.280680   
2                   1895            65.870040       154.239960   
3                   2613            72.776673       -27.776673   
4                   1592            95.178091       -53.218091   

   ft_transaction_count_per_user  
0                           2028  
1                           3030  
2                            503  
3                            493  
4                           2017  

[5 rows x 38 columns]

In [13]:
# Calculate the fraud rate for each state by dividing the number of fraudulent transactions by the total number of transactions
fraud_rate_by_state = ak_df.groupby('state')['is_fraud'].mean()
ak_df['ft_state_fraud_rate'] = ak_df['state'].map(fraud_rate_by_state)

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_trans_day_of_year  \
0    Banks      F                561 Perry Cove  ...                    1   
1     Gill      F  43039 Riley Greens Suite 393  ...                    1   
2  Sanchez      M      594 White Dale Suite 530  ...                    1   
3    White      M   9443 Cynthia Court Apt. 038  ...                    1   
4   Garcia      M              408 Bradley Rest  ...                    1   

  ft_trans_month  ft_day_of_week  ft_distance_user_merchant  \
0              1         Tuesday                  78.597568   
1              1         Tuesday                  30.212176   
2              1         Tuesday                 108.206083   
3              1         Tuesday                  95.673231   
4              1         Tuesday                  77.556744   

   ft_merchant_distance_from_user_mean  ft_merchant_popularity  \
0                             0.637376                    1267   
1                           -41.580370                    2503   
2                            34.130756                    1895   
3                            23.971060                    2613   
4                             2.322402                    1592   

  ft_mean_amt_per_user ft_amt_deviation ft_transaction_count_per_user  \
0            87.393215       -82.423215                          2028   
1            53.949320        53.280680                          3030   
2            65.870040       154.239960                           503   
3            72.776673       -27.776673                           493   
4            95.178091       -53.218091                          2017   

   ft_state_fraud_rate  
0             0.004923  
1             0.005073  
2             0.001984  
3             0.002722  
4             0.006769  

[5 rows x 39 columns]

In [14]:
# Flag transactions as recurring if the same merchant and cc_num combination appears multiple times within a short period
ak_df['ft_transaction_is_recurring'] = ak_df.duplicated(subset=['cc_num', 'merchant'], keep=False).astype(int)

ak_df.head()

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2019-01-01 00:00:18  2703186189652095   
1           1   2019-01-01 00:00:44      630423337322   
2           2   2019-01-01 00:00:51    38859492057661   
3           3   2019-01-01 00:01:16  3534093764340240   
4           4   2019-01-01 00:03:06   375534208663984   

                             merchant       category     amt      first  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97   Jennifer   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23  Stephanie   
2                fraud_Lind-Buckridge  entertainment  220.11     Edward   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00     Jeremy   
4                 fraud_Keeling-Crist       misc_pos   41.96      Tyler   

      last gender                        street  ... ft_trans_month  \
0    Banks      F                561 Perry Cove  ...              1   
1     Gill      F  43039 Riley Greens Suite 393  ...              1   
2  Sanchez      M      594 White Dale Suite 530  ...              1   
3    White      M   9443 Cynthia Court Apt. 038  ...              1   
4   Garcia      M              408 Bradley Rest  ...              1   

  ft_day_of_week  ft_distance_user_merchant  \
0        Tuesday                  78.597568   
1        Tuesday                  30.212176   
2        Tuesday                 108.206083   
3        Tuesday                  95.673231   
4        Tuesday                  77.556744   

   ft_merchant_distance_from_user_mean  ft_merchant_popularity  \
0                             0.637376                    1267   
1                           -41.580370                    2503   
2                            34.130756                    1895   
3                            23.971060                    2613   
4                             2.322402                    1592   

   ft_mean_amt_per_user ft_amt_deviation ft_transaction_count_per_user  \
0             87.393215       -82.423215                          2028   
1             53.949320        53.280680                          3030   
2             65.870040       154.239960                           503   
3             72.776673       -27.776673                           493   
4             95.178091       -53.218091                          2017   

  ft_state_fraud_rate  ft_transaction_is_recurring  
0            0.004923                            1  
1            0.005073                            1  
2            0.001984                            1  
3            0.002722                            0  
4            0.006769                            1  

[5 rows x 40 columns]

In [15]:
# lets review the current columns of the updated dataframe
ak_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1296675 entries, 0 to 1296674
Data columns (total 40 columns):
 #   Column                               Non-Null Count    Dtype         
---  ------                               --------------    -----         
 0   Unnamed: 0                           1296675 non-null  int64         
 1   trans_date_trans_time                1296675 non-null  datetime64[ns]
 2   cc_num                               1296675 non-null  int64         
 3   merchant                             1296675 non-null  object        
 4   category                             1296675 non-null  object        
 5   amt                                  1296675 non-null  float64       
 6   first                                1296675 non-null  object        
 7   last                                 1296675 non-null  object        
 8   gender                               1296675 non-null  object        
 9   street                               1296675 non-null  ob

In [16]:
# Drop unnecessary columns
columns_to_drop = [
    'Unnamed: 0', 'trans_date_trans_time', 'cc_num', 'first', 'last', 'street', 'trans_num', 'lat', 
    'long', 'merch_zipcode', 'ft_age', 'merch_lat', 'merch_long', 'trans_num', 'unix_time', 'zip', 'dob'
]
ak_df_cleaned = ak_df.drop(columns=columns_to_drop)

ak_df_cleaned.head()

# Check for null values
# print(ak_df_cleaned.isnull().sum())

merchant       category     amt gender  \
0          fraud_Rippin, Kub and Mann       misc_net    4.97      F   
1     fraud_Heller, Gutmann and Zieme    grocery_pos  107.23      F   
2                fraud_Lind-Buckridge  entertainment  220.11      M   
3  fraud_Kutch, Hermiston and Farrell  gas_transport   45.00      M   
4                 fraud_Keeling-Crist       misc_pos   41.96      M   

             city state  city_pop                                job  \
0  Moravian Falls    NC      3495          Psychologist, counselling   
1          Orient    WA       149  Special educational needs teacher   
2      Malad City    ID      4154        Nature conservation officer   
3         Boulder    MT      1939                    Patent attorney   
4        Doe Hill    VA        99     Dance movement psychotherapist   

   is_fraud ft_age_group  ...  ft_trans_month ft_day_of_week  \
0         0        29-38  ...               1        Tuesday   
1         0        39-48  ...               1        Tuesday   
2         0        49-58  ...               1        Tuesday   
3         0        49-58  ...               1        Tuesday   
4         0        29-38  ...               1        Tuesday   

   ft_distance_user_merchant  ft_merchant_distance_from_user_mean  \
0                  78.597568                             0.637376   
1                  30.212176                           -41.580370   
2                 108.206083                            34.130756   
3                  95.673231                            23.971060   
4                  77.556744                             2.322402   

   ft_merchant_popularity ft_mean_amt_per_user  ft_amt_deviation  \
0                    1267            87.393215        -82.423215   
1                    2503            53.949320         53.280680   
2                    1895            65.870040        154.239960   
3                    2613            72.776673        -27.776673   
4                    1592            95.178091        -53.218091   

   ft_transaction_count_per_user  ft_state_fraud_rate  \
0                           2028             0.004923   
1                           3030             0.005073   
2                            503             0.001984   
3                            493             0.002722   
4                           2017             0.006769   

   ft_transaction_is_recurring  
0                            1  
1                            1  
2                            1  
3                            0  
4                            1  

[5 rows x 24 columns]

In [17]:
# Explore data columns
ak_df_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1296675 entries, 0 to 1296674
Data columns (total 24 columns):
 #   Column                               Non-Null Count    Dtype  
---  ------                               --------------    -----  
 0   merchant                             1296675 non-null  object 
 1   category                             1296675 non-null  object 
 2   amt                                  1296675 non-null  float64
 3   gender                               1296675 non-null  object 
 4   city                                 1296675 non-null  object 
 5   state                                1296675 non-null  object 
 6   city_pop                             1296675 non-null  int64  
 7   job                                  1296675 non-null  object 
 8   is_fraud                             1296675 non-null  int64  
 9   ft_age_group                         1296675 non-null  object 
 10  ft_trans_hour                        1296675 non-null  int32  
 11

In [19]:
# Setup X and y variables
X = ak_df_cleaned.drop(columns='is_fraud')
y = ak_df_cleaned['is_fraud'].values.reshape(-1,1)

# Split the data into training and testing sets
X_train1, X_test, y_train1, y_test = train_test_split(X, y, test_size=0.1 ,random_state=42)
X_train, X_validation, y_train, y_validation = train_test_split(X_train1, y_train1, random_state=42)

X_train.describe()

amt      city_pop  ft_trans_hour   ft_trans_day  \
count  875255.000000  8.752550e+05  875255.000000  875255.000000   
mean       70.289636  8.885943e+04      12.805973      15.591315   
std       161.038519  3.017526e+05       6.815471       8.830291   
min         1.000000  2.300000e+01       0.000000       1.000000   
25%         9.670000  7.430000e+02       7.000000       8.000000   
50%        47.550000  2.456000e+03      14.000000      15.000000   
75%        83.180000  2.032800e+04      19.000000      23.000000   
max     28948.900000  2.906700e+06      23.000000      31.000000   

       ft_trans_day_of_year  ft_trans_month  ft_distance_user_merchant  \
count         875255.000000   875255.000000              875255.000000   
mean             171.276758        6.140808                  76.101950   
std              104.349248        3.416813                  29.113521   
min                1.000000        1.000000                   0.093922   
25%               87.000000        3.000000                  55.324579   
50%              155.000000        6.000000                  78.228994   
75%              255.000000        9.000000                  98.485766   
max              365.000000       12.000000                 152.117173   

       ft_merchant_distance_from_user_mean  ft_merchant_popularity  \
count                        875255.000000           875255.000000   
mean                             -0.013551             2048.188991   
std                              29.025146              529.972298   
min                             -80.831303              727.000000   
25%                             -20.698330             1783.000000   
50%                               2.182731             1985.000000   
75%                              22.251355             2444.000000   
max                              70.815341             4403.000000   

       ft_mean_amt_per_user  ft_amt_deviation  ft_transaction_count_per_user  \
count         875255.000000     875255.000000                  875255.000000   
mean              70.340711         -0.051075                    1818.577768   
std               19.431438        159.856002                     742.649295   
min               42.951671       -764.763750                       7.000000   
25%               59.800213        -52.441447                    1466.000000   
50%               65.093740        -24.035525                    2000.000000   
75%               82.894980         12.562201                    2524.000000   
max              948.818182      28873.996302                    3123.000000   

       ft_state_fraud_rate  ft_transaction_is_recurring  
count        875255.000000                875255.000000  
mean              0.005789                     0.880249  
std               0.002865                     0.324671  
min               0.001984                     0.000000  
25%               0.005149                     1.000000  
50%               0.005693                     1.000000  
75%               0.006585                     1.000000  
max               1.000000                     1.000000

In [20]:
!pip install category-encoders

In [21]:
import category_encoders as ce

# Define categorical columns to encode
categorical_columns = ['merchant', 'category', 'gender', 'city', 'state', 
                       'job', 'ft_time_of_day', 'ft_age_group', 'ft_day_of_week']

# Initialize the target encoder
encoder = ce.TargetEncoder(cols=categorical_columns)

# Fit the encoder on X_train using y_train
X_train_encoded = encoder.fit_transform(X_train, y_train)
X_train_encoded.head()

merchant  category    amt    gender      city     state  city_pop  \
993968   0.005161  0.004716  68.95  0.005266  0.002158  0.005537       139   
1194466  0.001880  0.001614  82.84  0.006372  0.004425  0.006557      1453   
197622   0.003840  0.004716  45.97  0.006372  0.000000  0.005193    116001   
329260   0.003728  0.003030  35.55  0.006372  0.005000  0.005565       795   
714316   0.002410  0.002389  12.15  0.005266  0.008759  0.004392      2456   

              job  ft_age_group  ft_trans_hour  ...  ft_trans_month  \
993968   0.007501      0.006654              8  ...               2   
1194466  0.001954      0.004130             23  ...               5   
197622   0.000000      0.005988              4  ...               4   
329260   0.007244      0.004579              4  ...               6   
714316   0.012922      0.005988             14  ...              11   

         ft_day_of_week  ft_distance_user_merchant  \
993968         0.004693                  25.711837   
1194466        0.006577                  60.318251   
197622         0.006991                  64.153784   
329260         0.006909                  86.365736   
714316         0.006991                 130.688611   

         ft_merchant_distance_from_user_mean  ft_merchant_popularity  \
993968                            -50.067674                    2641   
1194466                           -13.413125                    2341   
197622                            -13.583969                    2678   
329260                             13.417066                    1582   
714316                             55.007456                    1807   

         ft_mean_amt_per_user  ft_amt_deviation  \
993968              61.871168          7.078832   
1194466             97.602465        -14.762465   
197622              61.917571        -15.947571   
329260              92.048710        -56.498710   
714316              55.221352        -43.071352   

         ft_transaction_count_per_user  ft_state_fraud_rate  \
993968                            2037             0.005736   
1194466                           2049             0.006647   
197622                            2561             0.005362   
329260                            2093             0.005550   
714316                            2042             0.004796   

         ft_transaction_is_recurring  
993968                             1  
1194466                            1  
197622                             1  
329260                             1  
714316                             1  

[5 rows x 23 columns]

In [22]:
# Transform X_test using the already fitted encoder
X_test_encoded = encoder.transform(X_test)

# Check the transformed X_test
X_test_encoded.head()

merchant  category     amt    gender      city     state  city_pop  \
1045211  0.002887  0.003030  194.51  0.006372  0.000000  0.005537       972   
547406   0.000847  0.001414   52.32  0.005266  0.012380  0.008031       217   
110142   0.008521  0.007036    6.53  0.005266  0.000000  0.005537       184   
1285953  0.001226  0.001614    7.33  0.006372  0.000000  0.006557     10717   
271705   0.004970  0.004716   64.29  0.005266  0.008996  0.006371       635   

              job  ft_age_group  ft_trans_hour  ...  ft_trans_month  \
1045211  0.005549      0.005988             15  ...               3   
547406   0.005698      0.009190             15  ...               8   
110142   0.001157      0.007238              1  ...               3   
1285953  0.001183      0.006654             20  ...               6   
271705   0.004358      0.004130              5  ...               5   

         ft_day_of_week  ft_distance_user_merchant  \
1045211        0.004693                  54.336119   
547406         0.006909                  66.060865   
110142         0.004693                  94.386045   
1285953        0.005660                 109.251290   
271705         0.005660                  67.501516   

         ft_merchant_distance_from_user_mean  ft_merchant_popularity  \
1045211                           -22.093350                    1524   
547406                             -6.639384                    1751   
110142                             17.820994                    2362   
1285953                            35.316763                    2456   
271705                             -6.773677                    2676   

         ft_mean_amt_per_user  ft_amt_deviation  \
1045211             69.821821        124.688179   
547406              64.054238        -11.734238   
110142              63.390640        -56.860640   
1285953             69.869291        -62.539291   
271705              50.852975         13.437025   

         ft_transaction_count_per_user  ft_state_fraud_rate  \
1045211                           1494             0.005736   
547406                            1043             0.008012   
110142                            2062             0.005736   
1285953                           1496             0.006647   
271705                             995             0.005693   

         ft_transaction_is_recurring  
1045211                            1  
547406                             1  
110142                             1  
1285953                            1  
271705                             1  

[5 rows x 23 columns]

In [23]:
from sklearn.preprocessing import StandardScaler

# Initialize the StandardScaler
scaler = StandardScaler()

# Fit the scaler on X_train_encoded and transform it
X_train_scaled = scaler.fit_transform(X_train_encoded)
print("X_train scaled sample:")
print(X_train_scaled[:5])  # Display the first 5 rows of the scaled training data

# Transform X_test_encoded using the fitted scaler
X_test_scaled = scaler.transform(X_test_encoded)
print("X_test scaled sample:")
print(X_test_scaled[:5])  # Display the first 5 rows of the scaled testing data

X_train scaled sample:
[[-0.10776812 -0.19882275 -0.00831873 -0.90893792 -0.46342998 -0.17097327
  -0.29401729  0.34444114  0.58797112 -0.70515682 -1.00369582 -0.63319742
  -1.2484693  -1.21189254 -1.21977268 -1.73081579 -1.7245099   1.11857044
  -0.4358683   0.04460208  0.29411239 -0.01845019  0.36883965]
 [-0.69144133 -0.78624224  0.07793397  1.10018515 -0.14235729  0.60738705
  -0.28966272 -0.68165575 -1.0837832   1.49571948  1.01427476 -0.29345759
  -0.35723094 -0.33388092  0.92130448 -0.54214357 -0.46165424  0.5525028
   1.40297232 -0.09202906  0.31027076  0.29937168  0.36883965]
 [-0.34272921 -0.19882275 -0.15101759  1.10018515 -0.76917054 -0.43298392
   0.08994647 -1.04302257  0.14706631 -1.29205717  0.96798669 -0.4067042
  -0.6638936  -0.62655146  1.39139645 -0.41039945 -0.46754031  1.18838545
  -0.43348027 -0.09944265  0.99969482 -0.14909638  0.36883965]
 [-0.36264699 -0.51818135 -0.21572265  1.10018515 -0.06087156 -0.14913338
  -0.29184332  0.29677884 -0.78644365 -1.29205717 

In [24]:
y1 = pd.DataFrame(y_train)

df_corr = pd.concat([X_train_encoded.reset_index(),y1.reset_index()], axis=1, ignore_index=True)
df_corr.drop(columns=[24,25], inplace=True)

columns = [col for col in X_train_encoded.columns]
columns.append('Result')

df_corr.columns = columns 
df_corr.head()

merchant  category       amt  gender      city     state  city_pop     job  \
0    993968  0.005161  0.004716   68.95  0.005266  0.002158  0.005537     139   
1   1194466  0.001880  0.001614   82.84  0.006372  0.004425  0.006557    1453   
2    197622  0.003840  0.004716   45.97  0.006372  0.000000  0.005193  116001   
3    329260  0.003728  0.003030   35.55  0.006372  0.005000  0.005565     795   
4    714316  0.002410  0.002389   12.15  0.005266  0.008759  0.004392    2456   

   ft_age_group  ft_trans_hour  ...  ft_day_of_week  \
0      0.007501       0.006654  ...               2   
1      0.001954       0.004130  ...               5   
2      0.000000       0.005988  ...               4   
3      0.007244       0.004579  ...               6   
4      0.012922       0.005988  ...              11   

   ft_distance_user_merchant  ft_merchant_distance_from_user_mean  \
0                   0.004693                            25.711837   
1                   0.006577                            60.318251   
2                   0.006991                            64.153784   
3                   0.006909                            86.365736   
4                   0.006991                           130.688611   

   ft_merchant_popularity  ft_mean_amt_per_user  ft_amt_deviation  \
0              -50.067674                  2641         61.871168   
1              -13.413125                  2341         97.602465   
2              -13.583969                  2678         61.917571   
3               13.417066                  1582         92.048710   
4               55.007456                  1807         55.221352   

   ft_transaction_count_per_user  ft_state_fraud_rate  \
0                       7.078832                 2037   
1                     -14.762465                 2049   
2                     -15.947571                 2561   
3                     -56.498710                 2093   
4                     -43.071352                 2042   

   ft_transaction_is_recurring  Result  
0                     0.005736       1  
1                     0.006647       1  
2                     0.005362       1  
3                     0.005550       1  
4                     0.004796       1  

[5 rows x 24 columns]

In [25]:
columns_corr = df_corr.corr()['Result'].sort_values()

columns_corr

state                                 -0.188662
ft_age_group                          -0.140270
ft_trans_hour                         -0.091808
ft_amt_deviation                      -0.068689
city                                  -0.048692
city_pop                              -0.039823
ft_transaction_is_recurring           -0.023963
gender                                -0.008430
job                                   -0.002138
ft_trans_day                          -0.001341
ft_distance_user_merchant             -0.001005
ft_merchant_popularity                -0.000932
ft_trans_day_of_year                  -0.000873
ft_merchant_distance_from_user_mean   -0.000645
merchant                              -0.000171
ft_transaction_count_per_user         -0.000143
ft_trans_month                         0.000434
ft_day_of_week                         0.000509
amt                                    0.013204
category                               0.013293
ft_time_of_day                         0

In [26]:
sorted_columns = [item[0] for item in columns_corr.items()]

print(sorted_columns)

['state', 'ft_age_group', 'ft_trans_hour', 'ft_amt_deviation', 'city', 'city_pop', 'ft_transaction_is_recurring', 'gender', 'job', 'ft_trans_day', 'ft_distance_user_merchant', 'ft_merchant_popularity', 'ft_trans_day_of_year', 'ft_merchant_distance_from_user_mean', 'merchant', 'ft_transaction_count_per_user', 'ft_trans_month', 'ft_day_of_week', 'amt', 'category', 'ft_time_of_day', 'ft_mean_amt_per_user', 'ft_state_fraud_rate', 'Result']


In [29]:
def cost_of_error_by_chebyshevs(x, y_real, y_prediction, cost=0.25 ):
    
    false_negative_cost = []
    false_positive_cost = []
    correct = []
    
    size = len(y_real)
    
    for i in range(0, size-1):
        if ( y_real[i][0] != y_prediction[i])  :
            if (y_real[i][0] == np.int64(1)):
                false_negative_cost.append(x[i])
            else:
                false_positive_cost.append(x[i])
        else:
            if ( y_real[i][0] == np.int64(1)):
                correct.append(x[i])
    
    cost_correct_pred = (sum(correct)*len(correct))
    cost_fp_pred = (cost * sum(false_positive_cost) * (len(false_positive_cost)))
    cost_fn_pred = ( sum(false_negative_cost) * (len(false_negative_cost)) )
    
    return  { 
                'accuracy' : len(correct)/(len(correct) + len(false_positive_cost) + len(false_negative_cost) ),
                'error_cost' : cost_fn_pred/(cost_correct_pred + cost_fn_pred), 
                'error' : len(false_negative_cost)/(len(correct) + len(false_positive_cost) + len(false_negative_cost) ),
                'customer_experience_cost' : 1 - (cost_correct_pred/(cost_correct_pred + cost_fp_pred)),  
                'customer_experience_rating' : 1 - (len(false_positive_cost)/(len(correct) + len(false_positive_cost) + len(false_negative_cost) ))
        }

In [30]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.ensemble import StackingClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import HistGradientBoostingClassifier
from catboost import CatBoostClassifier
#from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, ExtraTreesClassifier

estimators = [
    ('rf', RandomForestClassifier(n_estimators=10, random_state=42)),
    ('svr', make_pipeline(StandardScaler(),
                          LinearSVC(random_state=42))),
    ('cbc', CatBoostClassifier(random_state=42)),
    ('abc', AdaBoostClassifier(random_state=42)),
    ('hgbc', HistGradientBoostingClassifier(random_state=42))
]


In [31]:
train_X = X_train_encoded.copy()
test_X = X_test_encoded.copy()

In [32]:
feature_sel_res = []
counter = 0
removed_cols = 'None'

for col in sorted_columns:
    
    print(f'{counter+1} Removed column: {removed_cols}')
    
    clfModel = StackingClassifier(
        estimators=estimators, final_estimator=LogisticRegression(random_state=42,)
    )
    
    clfModel.fit(train_X, y_train)
    
    y_train_pred2 = clfModel.predict(train_X)
    train_recall_score = recall_score(y_train, y_train_pred2)
    
    y_test_pred2 = clfModel.predict(test_X)
    test_recall_score = recall_score(y_test, y_test_pred2)
    
    train_model_rating2 = None
    test_model_rating2 = None
    
    if('amt' in train_X.columns):
        train_model_rating2 = cost_of_error_by_chebyshevs(train_X['amt'].to_list(), y_train, y_train_pred2)       
        test_model_rating2 = cost_of_error_by_chebyshevs(test_X['amt'].to_list(),y_test, y_test_pred2)
    
    feature_sel_res.append({ 
                            'removed_col' : removed_cols, 
                            'train' : {'recall':train_recall_score, 'rating':train_model_rating2},
                            'test' : {'recall':test_recall_score, 'rating':test_model_rating2} 
                            })
    
    train_X.drop(columns = [col] ,  inplace=True)
    test_X.drop(columns = [col] ,  inplace=True)
    removed_cols = col
    
    counter = counter+1

1 Removed column: None


c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\preprocessing\_label.py:97: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\preprocessing\_label.py:132: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)


Learning rate set to 0.185877
0:	learn: 0.2773627	total: 365ms	remaining: 6m 4s
1:	learn: 0.1192477	total: 490ms	remaining: 4m 4s
2:	learn: 0.0549701	total: 603ms	remaining: 3m 20s
3:	learn: 0.0322359	total: 727ms	remaining: 3m 1s
4:	learn: 0.0227629	total: 849ms	remaining: 2m 48s
5:	learn: 0.0185692	total: 959ms	remaining: 2m 38s
6:	learn: 0.0164288	total: 1.06s	remaining: 2m 30s
7:	learn: 0.0143649	total: 1.19s	remaining: 2m 27s
8:	learn: 0.0127930	total: 1.31s	remaining: 2m 24s
9:	learn: 0.0119917	total: 1.44s	remaining: 2m 22s
10:	learn: 0.0116484	total: 1.55s	remaining: 2m 19s
11:	learn: 0.0111195	total: 1.98s	remaining: 2m 43s
12:	learn: 0.0107481	total: 2.22s	remaining: 2m 48s
13:	learn: 0.0104130	total: 2.4s	remaining: 2m 49s
14:	learn: 0.0100897	total: 2.59s	remaining: 2m 49s
15:	learn: 0.0099158	total: 2.76s	remaining: 2m 49s
16:	learn: 0.0096141	total: 2.92s	remaining: 2m 48s
17:	learn: 0.0091699	total: 3.07s	remaining: 2m 47s
18:	learn: 0.0090195	total: 3.26s	remaining: 2m 

c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(


Learning rate set to 0.168984
0:	learn: 0.3018140	total: 94.8ms	remaining: 1m 34s
1:	learn: 0.1372277	total: 204ms	remaining: 1m 41s
2:	learn: 0.0639049	total: 336ms	remaining: 1m 51s
3:	learn: 0.0384647	total: 431ms	remaining: 1m 47s
4:	learn: 0.0264229	total: 544ms	remaining: 1m 48s
5:	learn: 0.0199606	total: 647ms	remaining: 1m 47s
6:	learn: 0.0165741	total: 760ms	remaining: 1m 47s
7:	learn: 0.0145278	total: 867ms	remaining: 1m 47s
8:	learn: 0.0130005	total: 964ms	remaining: 1m 46s
9:	learn: 0.0120244	total: 1.06s	remaining: 1m 44s
10:	learn: 0.0113387	total: 1.18s	remaining: 1m 45s
11:	learn: 0.0109214	total: 1.28s	remaining: 1m 45s
12:	learn: 0.0105015	total: 1.39s	remaining: 1m 45s
13:	learn: 0.0101511	total: 1.51s	remaining: 1m 46s
14:	learn: 0.0099316	total: 1.62s	remaining: 1m 46s
15:	learn: 0.0097023	total: 1.74s	remaining: 1m 46s
16:	learn: 0.0094319	total: 1.84s	remaining: 1m 46s
17:	learn: 0.0092539	total: 1.95s	remaining: 1m 46s
18:	learn: 0.0090712	total: 2.06s	remaining

...

Learning rate set to 0.168984
0:	learn: 0.3542890	total: 69.3ms	remaining: 1m 9s
1:	learn: 0.1935448	total: 140ms	remaining: 1m 10s
2:	learn: 0.1177921	total: 203ms	remaining: 1m 7s
3:	learn: 0.0805775	total: 279ms	remaining: 1m 9s
4:	learn: 0.0613140	total: 349ms	remaining: 1m 9s
5:	learn: 0.0508165	total: 413ms	remaining: 1m 8s
6:	learn: 0.0448290	total: 480ms	remaining: 1m 8s
7:	learn: 0.0412870	total: 550ms	remaining: 1m 8s
8:	learn: 0.0391350	total: 625ms	remaining: 1m 8s
9:	learn: 0.0377996	total: 697ms	remaining: 1m 9s
10:	learn: 0.0369482	total: 760ms	remaining: 1m 8s
11:	learn: 0.0364010	total: 814ms	remaining: 1m 6s
12:	learn: 0.0360463	total: 882ms	remaining: 1m 6s
13:	learn: 0.0358079	total: 948ms	remaining: 1m 6s
14:	learn: 0.0356514	total: 1.02s	remaining: 1m 6s
15:	learn: 0.0355450	total: 1.08s	remaining: 1m 6s
16:	learn: 0.0354748	total: 1.15s	remaining: 1m 6s
17:	learn: 0.0354244	total: 1.21s	remaining: 1m 6s
18:	learn: 0.0353873	total: 1.27s	remaining: 1m 5s
19:	learn

c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(
c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(
c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(
c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\ensemble\_weight_boosting.py:527: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  war

24 Removed column: ft_state_fraud_rate


c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\preprocessing\_label.py:97: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\deepa\.conda\envs\dev\Lib\site-packages\sklearn\preprocessing\_label.py:132: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)


ValueError: at least one array or dtype is required

In [33]:
first_iter = True
cols = 'None'
for res in feature_sel_res:
    print(f'Removed columns : {res['removed_col']} train: {res['train']['recall']} - test: {res['test']['recall']}')
    if first_iter == False:
        print(f'Train % change: {100*((res['train']['recall']*100 - prev_train_recall)/prev_train_recall )} - Test % change: {100*((res['test']['recall']*100 -prev_test_recall)/prev_test_recall)}')
    prev_train_recall = res['train']['recall']*100
    prev_test_recall = res['test']['recall']*100
    first_iter = False

Removed columns : None train: 0.9774123241529622 - test: 0.8447606727037517
Removed columns : state train: 0.9799881117495541 - test: 0.8525226390685641
Train % change: 0.26353131968375526 - Test % change: 0.918836140888212
Removed columns : ft_age_group train: 0.9793936992272637 - test: 0.8227684346701164
Train % change: -0.060655074807928415 - Test % change: -3.4901365705614653
Removed columns : ft_trans_hour train: 0.9647315236774321 - test: 0.796895213454075
Train % change: -1.4970665587699796 - Test % change: -3.1446540880503213
Removed columns : ft_amt_deviation train: 0.9631464236179909 - test: 0.7943078913324709
Train % change: -0.16430478537687193 - Test % change: -0.3246753246753201
Removed columns : city train: 0.9564097483653655 - test: 0.795601552393273
Train % change: -0.6994445587327692 - Test % change: 0.1628664495114073
Removed columns : city_pop train: 0.9486823855755895 - test: 0.7813712807244502
Train % change: -0.8079552517091292 - Test % change: -1.788617886178863